# **CARBON EMISSION PREDICTION**

# **LSTM (LONG SHORT TERM MEMORY) MODEL**

In [2]:
# IMPORT THE REQUIRED LIBRARIES

import os
import numpy as np
import pandas as pd
import tensorflow as tf
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_absolute_percentage_error
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, SimpleRNN, GRU, Dense

In [3]:
#Importing the dataset

data = pd.read_csv("/content/drive/MyDrive/MY PROJECTS/CARBON EMISSION/Emission/new_data.csv")
data.head()

year state-name                          sector-name  fuel-name     value
0  1970    Alabama  Commercial carbon dioxide emissions  Petroleum  0.824345
1  1971    Alabama  Commercial carbon dioxide emissions  Petroleum  0.796784
2  1972    Alabama  Commercial carbon dioxide emissions  Petroleum  0.867950
3  1973    Alabama  Commercial carbon dioxide emissions  Petroleum  0.976399
4  1974    Alabama  Commercial carbon dioxide emissions  Petroleum  0.856390

In [4]:
data.shape

(10376, 5)

In [5]:
unique_combinations = data[["state-name", "sector-name", "fuel-name"]].drop_duplicates()

In [6]:
unique_combinations

state-name                                      sector-name    fuel-name
0        Alabama              Commercial carbon dioxide emissions    Petroleum
52       Alabama              Commercial carbon dioxide emissions  Natural Gas
104      Alabama          Electric Power carbon dioxide emissions  Natural Gas
156       Alaska              Commercial carbon dioxide emissions    Petroleum
208       Alaska              Commercial carbon dioxide emissions    All Fuels
...          ...                                              ...          ...
10121    Wyoming             Residential carbon dioxide emissions    Petroleum
10173    Wyoming              Commercial carbon dioxide emissions    Petroleum
10225   Arkansas  Total carbon dioxide emissions from all sectors         Coal
10276  Tennessee          Electric Power carbon dioxide emissions    Petroleum
10327    Vermont          Electric Power carbon dioxide emissions  Natural Gas

[200 rows x 3 columns]

In [10]:
# Initialize an empty list to store error results
error_results = []

# Define the folder to save the trained models
trained_models_folder = "/content/drive/MyDrive/MY PROJECTS/CARBON EMISSION/lstm"

# Create the folder if it doesn't exist
if not os.path.exists(trained_models_folder):
    os.makedirs(trained_models_folder)

# Iterate over each unique combination
for idx, row in unique_combinations.iterrows():
    state_name = row['state-name']
    sector_name = row['sector-name']
    fuel_name = row['fuel-name']

    # Filter the dataset for the current combination
    filtered_data = data[(data['state-name'] == state_name) &
                         (data['fuel-name'] == fuel_name) &
                         (data['sector-name'] == sector_name)]

    # Prepare the time series data
    time_series = filtered_data['value'].values.reshape(-1, 1)

    # Normalize the data
    scaler = MinMaxScaler(feature_range=(0, 1))
    scaled_data = scaler.fit_transform(time_series)

    # Split the time series into training and test sets
    train_size = 40  # Number of data points for training
    train, test = scaled_data[:train_size], scaled_data[train_size:]

    # Prepare the data for LSTM
    def create_dataset(X, y, time_steps=1):
        Xs, ys = [], []
        for i in range(len(X) - time_steps):
            v = X[i:(i + time_steps)]
            Xs.append(v)
            ys.append(y[i + time_steps])
        return np.array(Xs), np.array(ys)

    time_steps = 3  # Adjust the time steps as needed
    X_train, y_train = create_dataset(train, train, time_steps)
    X_test, y_test = create_dataset(test, test, time_steps)

    # Define the LSTM model
    model = Sequential()
    model.add(LSTM(units=50, activation='relu', input_shape=(time_steps, 1)))
    model.add(Dense(units=1))
    model.compile(optimizer='adam', loss='mse')

    # Train the model
    model.fit(X_train, y_train, epochs=100, batch_size=32, verbose=True)

    # Save the trained model to the folder
    model.save(os.path.join(trained_models_folder, f"model_{state_name}_{sector_name}_{fuel_name}.h5"))

    # Make predictions
    train_predictions = model.predict(X_train)
    test_predictions = model.predict(X_test)

    # Invert the predictions to original scale
    train_predictions = scaler.inverse_transform(train_predictions)
    y_train = scaler.inverse_transform(y_train.reshape(-1, 1))
    test_predictions = scaler.inverse_transform(test_predictions)
    y_test = scaler.inverse_transform(y_test.reshape(-1, 1))

    # Calculate MAPE for training and test sets
    train_mape = mean_absolute_percentage_error(y_train, train_predictions)
    test_mape = mean_absolute_percentage_error(y_test, test_predictions)

    # Store the error result
    error_results.append({
        'state-name': state_name,
        'sector-name': sector_name,
        'fuel-name': fuel_name,
        'train_mape': '{:.3f}'.format(train_mape),
        'test_mape': '{:.3f}'.format(test_mape)
    })

# Convert error_results list to a DataFrame
error_results_df = pd.DataFrame(error_results)


Epoch 1/100
2/2 [==============================] - 1s 7ms/step - loss: 0.2965
Epoch 2/100
2/2 [==============================] - 0s 5ms/step - loss: 0.2807
Epoch 3/100
2/2 [==============================] - 0s 5ms/step - loss: 0.2662
Epoch 4/100
2/2 [==============================] - 0s 5ms/step - loss: 0.2511
Epoch 5/100
2/2 [==============================] - 0s 5ms/step - loss: 0.2375
Epoch 6/100
2/2 [==============================] - 0s 5ms/step - loss: 0.2242
Epoch 7/100
2/2 [==============================] - 0s 5ms/step - loss: 0.2108
Epoch 8/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1977
Epoch 9/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1852
Epoch 10/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1729
Epoch 11/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1605
Epoch 12/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1494
Epoch 13/100
2/2 [==============================] - 0s 5ms/st

/usr/local/lib/python3.10/dist-packages/keras/src/engine/training.py:3103: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


1/1 [==============================] - 0s 25ms/step
Epoch 1/100
2/2 [==============================] - 1s 6ms/step - loss: 0.1761
Epoch 2/100
2/2 [==============================] - 0s 6ms/step - loss: 0.1667
Epoch 3/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1574
Epoch 4/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1489
Epoch 5/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1406
Epoch 6/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1326
Epoch 7/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1250
Epoch 8/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1174
Epoch 9/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1095
Epoch 10/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1028
Epoch 11/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0955
Epoch 12/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0888
Epoch 13/

/usr/local/lib/python3.10/dist-packages/keras/src/engine/training.py:3103: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


1/1 [==============================] - 0s 23ms/step
Epoch 1/100
2/2 [==============================] - 1s 6ms/step - loss: 0.0279
Epoch 2/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0264
Epoch 3/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0253
Epoch 4/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0240
Epoch 5/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0229
Epoch 6/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0217
Epoch 7/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0207
Epoch 8/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0199
Epoch 9/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0189
Epoch 10/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0181
Epoch 11/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0174
Epoch 12/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0167
Epoch 13/

...

1/1 [==============================] - 0s 23ms/step
Epoch 1/100
2/2 [==============================] - 1s 6ms/step - loss: 0.0583
Epoch 2/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0561
Epoch 3/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0541
Epoch 4/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0521
Epoch 5/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0504
Epoch 6/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0488
Epoch 7/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0472
Epoch 8/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0457
Epoch 9/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0442
Epoch 10/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0431
Epoch 11/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0419
Epoch 12/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0408
Epoch 13/

/usr/local/lib/python3.10/dist-packages/keras/src/engine/training.py:3103: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


1/1 [==============================] - 0s 24ms/step
Epoch 1/100
2/2 [==============================] - 1s 6ms/step - loss: 0.1034
Epoch 2/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1013
Epoch 3/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0990
Epoch 4/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0970
Epoch 5/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0948
Epoch 6/100
2/2 [==============================] - 0s 32ms/step - loss: 0.0927
Epoch 7/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0904
Epoch 8/100
2/2 [==============================] - 0s 6ms/step - loss: 0.0883
Epoch 9/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0863
Epoch 10/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0841
Epoch 11/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0821
Epoch 12/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0801
Epoch 13

/usr/local/lib/python3.10/dist-packages/keras/src/engine/training.py:3103: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


1/1 [==============================] - 0s 24ms/step


In [11]:
error_results_df

state-name                                      sector-name    fuel-name  \
0      Alabama              Commercial carbon dioxide emissions    Petroleum   
1      Alabama              Commercial carbon dioxide emissions  Natural Gas   
2      Alabama          Electric Power carbon dioxide emissions  Natural Gas   
3       Alaska              Commercial carbon dioxide emissions    Petroleum   
4       Alaska              Commercial carbon dioxide emissions    All Fuels   
..         ...                                              ...          ...   
195    Wyoming             Residential carbon dioxide emissions    Petroleum   
196    Wyoming              Commercial carbon dioxide emissions    Petroleum   
197   Arkansas  Total carbon dioxide emissions from all sectors         Coal   
198  Tennessee          Electric Power carbon dioxide emissions    Petroleum   
199    Vermont          Electric Power carbon dioxide emissions  Natural Gas   

    train_mape test_mape  
0        0.165     0.221  
1        0.056     0.057  
2        0.843     0.409  
3        0.406     0.203  
4        0.204     0.080  
..         ...       ...  
195      0.370     0.132  
196      0.248     0.193  
197      1.518     0.225  
198      0.674     0.916  
199      4.676    16.650  

[200 rows x 5 columns]

In [12]:

# Calculate overall train accuracy
total_train_points = 0
weighted_train_accuracy = 0
for result in error_results:
    train_points = len(train)
    total_train_points += train_points
    train_error = float(result['train_mape'])
    train_accuracy = 100 - train_error
    weighted_train_accuracy += train_accuracy * train_points

overall_train_accuracy_lstm = weighted_train_accuracy / total_train_points

# Calculate overall test accuracy
total_test_points = 0
weighted_test_accuracy = 0
for result in error_results:
    test_points = len(test)
    total_test_points += test_points
    test_error = float(result['test_mape'])
    test_accuracy = 100 - test_error
    weighted_test_accuracy += test_accuracy * test_points

overall_test_accuracy_lstm = weighted_test_accuracy / total_test_points

print("Overall Train Accuracy: {:.3f}%".format(overall_train_accuracy_lstm))
print("Overall Test Accuracy: {:.3f}%".format(overall_test_accuracy_lstm))

Overall Train Accuracy: 99.682%
Overall Test Accuracy: 98.397%


# **SIMPLE RNN (RECURRENT NEURAL NETWORK)**

In [13]:
# Initialize an empty list to store error results
error_results = []

# Define the folder to save the trained models
trained_models_folder = "/content/drive/MyDrive/MY PROJECTS/CARBON EMISSION/simple_rnn"

# Create the folder if it doesn't exist
if not os.path.exists(trained_models_folder):
    os.makedirs(trained_models_folder)

# Iterate over each unique combination
for idx, row in unique_combinations.iterrows():
    state_name = row['state-name']
    sector_name = row['sector-name']
    fuel_name = row['fuel-name']

    # Filter the dataset for the current combination
    filtered_data = data[(data['state-name'] == state_name) &
                         (data['fuel-name'] == fuel_name) &
                         (data['sector-name'] == sector_name)]

    # Prepare the time series data
    time_series = filtered_data['value'].values.reshape(-1, 1)

    # Normalize the data
    scaler = MinMaxScaler(feature_range=(0, 1))
    scaled_data = scaler.fit_transform(time_series)

    # Split the time series into training and test sets
    train_size = 40  # Number of data points for training
    train, test = scaled_data[:train_size], scaled_data[train_size:]

    # Prepare the data for SimpleRNN
    def create_dataset(X, y, time_steps=1):
        Xs, ys = [], []
        for i in range(len(X) - time_steps):
            v = X[i:(i + time_steps)]
            Xs.append(v)
            ys.append(y[i + time_steps])
        return np.array(Xs), np.array(ys)

    time_steps = 3  # Adjust the time steps as needed
    X_train, y_train = create_dataset(train, train, time_steps)
    X_test, y_test = create_dataset(test, test, time_steps)

    # Define the SimpleRNN model
    model = Sequential()
    model.add(SimpleRNN(units=50, activation='relu', input_shape=(time_steps, 1)))
    model.add(Dense(units=1))
    model.compile(optimizer='adam', loss='mse')

    # Train the model
    model.fit(X_train, y_train, epochs=100, batch_size=32, verbose=True)

    # Save the trained model to the folder
    model.save(os.path.join(trained_models_folder, f"model_{state_name}_{sector_name}_{fuel_name}.h5"))

    # Make predictions
    train_predictions = model.predict(X_train)
    test_predictions = model.predict(X_test)

    # Invert the predictions to original scale
    train_predictions = scaler.inverse_transform(train_predictions)
    y_train = scaler.inverse_transform(y_train.reshape(-1, 1))
    test_predictions = scaler.inverse_transform(test_predictions)
    y_test = scaler.inverse_transform(y_test.reshape(-1, 1))

    # Calculate MAPE for training and test sets
    train_mape = mean_absolute_percentage_error(y_train, train_predictions)
    test_mape = mean_absolute_percentage_error(y_test, test_predictions)

    # Store the error result
    error_results.append({
        'state-name': state_name,
        'sector-name': sector_name,
        'fuel-name': fuel_name,
        'train_mape': '{:.3f}'.format(train_mape),
        'test_mape': '{:.3f}'.format(test_mape)
    })

# Convert error_results list to a DataFrame
error_results_rnn = pd.DataFrame(error_results)


Epoch 1/100
2/2 [==============================] - 1s 6ms/step - loss: 0.1081
Epoch 2/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0867
Epoch 3/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0704
Epoch 4/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0590
Epoch 5/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0508
Epoch 6/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0494
Epoch 7/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0496
Epoch 8/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0510
Epoch 9/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0500
Epoch 10/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0491
Epoch 11/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0480
Epoch 12/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0473
Epoch 13/100
2/2 [==============================] - 0s 4ms/st

/usr/local/lib/python3.10/dist-packages/keras/src/engine/training.py:3103: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


1/1 [==============================] - 0s 22ms/step
Epoch 1/100
2/2 [==============================] - 1s 5ms/step - loss: 0.1900
Epoch 2/100
2/2 [==============================] - 0s 4ms/step - loss: 0.1600
Epoch 3/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1335
Epoch 4/100
2/2 [==============================] - 0s 4ms/step - loss: 0.1073
Epoch 5/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0850
Epoch 6/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0663
Epoch 7/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0493
Epoch 8/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0362
Epoch 9/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0260
Epoch 10/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0211
Epoch 11/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0195
Epoch 12/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0203
Epoch 13/

/usr/local/lib/python3.10/dist-packages/keras/src/engine/training.py:3103: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


1/1 [==============================] - 0s 23ms/step
Epoch 1/100
2/2 [==============================] - 1s 5ms/step - loss: 0.0239
Epoch 2/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0202
Epoch 3/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0172
Epoch 4/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0146
Epoch 5/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0125
Epoch 6/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0106
Epoch 7/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0089
Epoch 8/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0079
Epoch 9/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0069
Epoch 10/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0061
Epoch 11/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0055
Epoch 12/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0050
Epoch 13/

...

1/1 [==============================] - 0s 23ms/step
Epoch 1/100
2/2 [==============================] - 1s 5ms/step - loss: 0.0427
Epoch 2/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0399
Epoch 3/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0373
Epoch 4/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0356
Epoch 5/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0339
Epoch 6/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0327
Epoch 7/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0314
Epoch 8/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0303
Epoch 9/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0295
Epoch 10/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0287
Epoch 11/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0282
Epoch 12/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0277
Epoch 13/

/usr/local/lib/python3.10/dist-packages/keras/src/engine/training.py:3103: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


1/1 [==============================] - 0s 24ms/step
Epoch 1/100
2/2 [==============================] - 1s 6ms/step - loss: 0.0892
Epoch 2/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0786
Epoch 3/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0716
Epoch 4/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0686
Epoch 5/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0658
Epoch 6/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0636
Epoch 7/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0615
Epoch 8/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0600
Epoch 9/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0589
Epoch 10/100
2/2 [==============================] - 0s 4ms/step - loss: 0.0579
Epoch 11/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0568
Epoch 12/100
2/2 [==============================] - 0s 47ms/step - loss: 0.0552
Epoch 13

/usr/local/lib/python3.10/dist-packages/keras/src/engine/training.py:3103: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


1/1 [==============================] - 0s 25ms/step


In [14]:
# Calculate overall train accuracy
total_train_points = 0
weighted_train_accuracy = 0
for result in error_results:
    train_points = len(train)
    total_train_points += train_points
    train_error = float(result['train_mape'])
    train_accuracy = 100 - train_error
    weighted_train_accuracy += train_accuracy * train_points

overall_train_accuracy_rnn = weighted_train_accuracy / total_train_points

# Calculate overall test accuracy
total_test_points = 0
weighted_test_accuracy = 0
for result in error_results:
    test_points = len(test)
    total_test_points += test_points
    test_error = float(result['test_mape'])
    test_accuracy = 100 - test_error
    weighted_test_accuracy += test_accuracy * test_points

overall_test_accuracy_rnn = weighted_test_accuracy / total_test_points

print("Overall Train Accuracy: {:.3f}%".format(overall_train_accuracy_rnn))
print("Overall Test Accuracy: {:.3f}%".format(overall_test_accuracy_rnn))

Overall Train Accuracy: 99.759%
Overall Test Accuracy: 98.549%


# **GRU (GATED RECURRENT UNIT)**

In [7]:
# Initialize an empty list to store error results
error_results = []

# Define the folder to save the trained models
trained_models_folder = "/content/drive/MyDrive/MY PROJECTS/CARBON EMISSION/gru"

# Create the folder if it doesn't exist
if not os.path.exists(trained_models_folder):
    os.makedirs(trained_models_folder)

# Iterate over each unique combination
for idx, row in unique_combinations.iterrows():
    state_name = row['state-name']
    sector_name = row['sector-name']
    fuel_name = row['fuel-name']

    # Filter the dataset for the current combination
    filtered_data = data[(data['state-name'] == state_name) &
                             (data['fuel-name'] == fuel_name) &
                             (data['sector-name'] == sector_name)]

    # Prepare the time series data
    time_series = filtered_data['value'].values.reshape(-1, 1)

    # Normalize the data
    scaler = MinMaxScaler(feature_range=(0, 1))
    scaled_data = scaler.fit_transform(time_series)

    # Split the time series into training and test sets
    train_size = 40  # Number of data points for training
    train, test = scaled_data[:train_size], scaled_data[train_size:]

    # Prepare the data for GRU
    def create_dataset(X, y, time_steps=1):
        Xs, ys = [], []
        for i in range(len(X) - time_steps):
            v = X[i:(i + time_steps)]
            Xs.append(v)
            ys.append(y[i + time_steps])
        return np.array(Xs), np.array(ys)

    time_steps = 3  # Adjust the time steps as needed
    X_train, y_train = create_dataset(train, train, time_steps)
    X_test, y_test = create_dataset(test, test, time_steps)

    # Define the GRU model
    model = Sequential()
    model.add(GRU(units=50, activation='relu', input_shape=(time_steps, 1)))
    model.add(Dense(units=1))
    model.compile(optimizer='adam', loss='mse')

    # Train the model
    model.fit(X_train, y_train, epochs=100, batch_size=32, verbose=True)

    # Save the trained model to the folder
    model.save(os.path.join(trained_models_folder, f"model_{state_name}_{sector_name}_{fuel_name}.h5"))

    # Make predictions
    train_predictions = model.predict(X_train)
    test_predictions = model.predict(X_test)

    # Invert the predictions to original scale
    train_predictions = scaler.inverse_transform(train_predictions)
    y_train = scaler.inverse_transform(y_train.reshape(-1, 1))
    test_predictions = scaler.inverse_transform(test_predictions)
    y_test = scaler.inverse_transform(y_test.reshape(-1, 1))

    # Calculate MAPE for training and test sets
    train_mape = mean_absolute_percentage_error(y_train, train_predictions)
    test_mape = mean_absolute_percentage_error(y_test, test_predictions)

    # Store the error result
    error_results.append({
        'state-name': state_name,
        'sector-name': sector_name,
        'fuel-name': fuel_name,
        'train_mape': '{:.3f}'.format(train_mape),
        'test_mape': '{:.3f}'.format(test_mape)
    })

# Convert error_results list to a DataFrame
error_results_gru = pd.DataFrame(error_results)

Epoch 1/100
2/2 [==============================] - 1s 9ms/step - loss: 0.2790
Epoch 2/100
2/2 [==============================] - 0s 5ms/step - loss: 0.2542
Epoch 3/100
2/2 [==============================] - 0s 5ms/step - loss: 0.2313
Epoch 4/100
2/2 [==============================] - 0s 5ms/step - loss: 0.2095
Epoch 5/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1889
Epoch 6/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1700
Epoch 7/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1526
Epoch 8/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1357
Epoch 9/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1216
Epoch 10/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1081
Epoch 11/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0966
Epoch 12/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0856
Epoch 13/100
2/2 [==============================] - 0s 5ms/st

/usr/local/lib/python3.10/dist-packages/keras/src/engine/training.py:3103: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


1/1 [==============================] - 0s 23ms/step
Epoch 1/100
2/2 [==============================] - 1s 6ms/step - loss: 0.2346
Epoch 2/100
2/2 [==============================] - 0s 5ms/step - loss: 0.2195
Epoch 3/100
2/2 [==============================] - 0s 5ms/step - loss: 0.2056
Epoch 4/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1920
Epoch 5/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1801
Epoch 6/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1687
Epoch 7/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1578
Epoch 8/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1477
Epoch 9/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1382
Epoch 10/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1289
Epoch 11/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1199
Epoch 12/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1119
Epoch 13/

/usr/local/lib/python3.10/dist-packages/keras/src/engine/training.py:3103: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


1/1 [==============================] - 0s 24ms/step
Epoch 1/100
2/2 [==============================] - 1s 6ms/step - loss: 0.0267
Epoch 2/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0239
Epoch 3/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0220
Epoch 4/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0201
Epoch 5/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0185
Epoch 6/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0172
Epoch 7/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0162
Epoch 8/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0152
Epoch 9/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0143
Epoch 10/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0137
Epoch 11/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0131
Epoch 12/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0126
Epoch 13/

...

1/1 [==============================] - 0s 24ms/step
Epoch 1/100
2/2 [==============================] - 1s 6ms/step - loss: 0.0545
Epoch 2/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0516
Epoch 3/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0490
Epoch 4/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0467
Epoch 5/100
2/2 [==============================] - 0s 25ms/step - loss: 0.0444
Epoch 6/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0425
Epoch 7/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0404
Epoch 8/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0391
Epoch 9/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0377
Epoch 10/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0363
Epoch 11/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0356
Epoch 12/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0347
Epoch 13

/usr/local/lib/python3.10/dist-packages/keras/src/engine/training.py:3103: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


1/1 [==============================] - 0s 24ms/step
Epoch 1/100
2/2 [==============================] - 1s 49ms/step - loss: 0.1067
Epoch 2/100
2/2 [==============================] - 0s 5ms/step - loss: 0.1010
Epoch 3/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0957
Epoch 4/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0911
Epoch 5/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0870
Epoch 6/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0829
Epoch 7/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0794
Epoch 8/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0761
Epoch 9/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0725
Epoch 10/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0705
Epoch 11/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0684
Epoch 12/100
2/2 [==============================] - 0s 5ms/step - loss: 0.0663
Epoch 13

/usr/local/lib/python3.10/dist-packages/keras/src/engine/training.py:3103: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


1/1 [==============================] - 0s 25ms/step


In [8]:
# Calculate overall train accuracy
total_train_points = 0
total_train_accuracy = 0

for result in error_results:
    train_points = len(train)
    total_train_points += train_points
    train_error = float(result['train_mape'])
    train_accuracy = 100 - train_error
    total_train_accuracy += train_accuracy

overall_train_accuracy_gru = total_train_accuracy / len(error_results)

# Calculate overall test accuracy
total_test_points = 0
total_test_accuracy = 0

for result in error_results:
    test_points = len(test)
    total_test_points += test_points
    test_error = float(result['test_mape'])
    test_accuracy = 100 - test_error
    total_test_accuracy += test_accuracy

overall_test_accuracy_gru = total_test_accuracy / len(error_results)

print("Overall Train Accuracy: {:.3f}%".format(overall_train_accuracy_gru))
print("Overall Test Accuracy: {:.3f}%".format(overall_test_accuracy_gru))


Overall Train Accuracy: 99.698%
Overall Test Accuracy: 98.638%


In [26]:
# Accuracy of all model

train_acc = {'LSTM': overall_train_accuracy_lstm, 'SimpleRNN': overall_test_accuracy_rnn, 'GRU':overall_train_accuracy_gru }

In [27]:
train_acc = pd.DataFrame(train_acc, index = ['Train Accuracy'])
train_acc = train_acc.transpose().reset_index()

In [28]:
test_acc = {'LSTM': overall_test_accuracy_lstm, 'SimpleRNN': overall_train_accuracy_rnn, 'GRU':overall_test_accuracy_gru }

In [29]:
test_acc = pd.DataFrame(test_acc, index = ['Test Accuracy'])
test_acc = test_acc.transpose().reset_index()

In [30]:
Accuracy = pd.merge(train_acc, test_acc, on = 'index')
Accuracy = Accuracy.rename(columns = {'index' : 'Algorithms'})

In [31]:
Accuracy

Algorithms  Train Accuracy  Test Accuracy
0       LSTM       99.682180      98.397485
1  SimpleRNN       98.548990      99.758860
2        GRU       99.698165      98.637755